In [1]:
import numpy as np
import pandas as pd
import altair as alt
from pathlib import Path
import geopandas as gpd
from topojson import Topology
from shapely.geometry import Point,LineString
from preprocessing import *

In [2]:
linestring_dict = plottingUtils.selectTravelJournal('commute')

-------Reading Reduced Complete Logs------------
-------Done Reading Reduced Complete Logs-------
-------Processing Date Time----------------------
-------DONE Processing Date Time-----------------
--------Doing 0th ID--------
--------Doing 50th ID--------
--------Doing 100th ID--------
--------Doing 150th ID--------
--------Doing 200th ID--------
--------Doing 250th ID--------
162 did not work
--------Doing 300th ID--------
--------Doing 350th ID--------
--------Doing 400th ID--------
--------Doing 450th ID--------
--------Doing 500th ID--------
--------Doing 550th ID--------
--------Doing 600th ID--------
--------Doing 650th ID--------
--------Doing 700th ID--------
--------Doing 750th ID--------
--------Doing 800th ID--------
--------Doing 850th ID--------
--------Doing 900th ID--------
COMPLETED COLLECTING LINESTRINGS


Plotting Main Map

In [4]:
file_path = r'D:\Datasets\Projects\VAST Challenge\VAST-Challenge-2022\Datasets\Attributes'
buildings_df = pd.read_csv(Path(Path(file_path,'Buildings.csv')))
cluster_df = pd.read_csv(r"..\parallelCoordsExpense.csv")[['pID','Cluster']]

In [5]:
cluster_df

pID  Cluster
0        0        1
1        1        1
2        2        1
3        3        1
4        4        1
...    ...      ...
1006  1006        1
1007  1007        1
1008  1008        1
1009  1009        1
1010  1010        1

[1011 rows x 2 columns]

In [6]:
buildings_df = buildings_df[["buildingId","location","buildingType"]]
buildings_df['geometry'] = gpd.GeoSeries.from_wkt(buildings_df['location'])

In [7]:
gdf = gpd.GeoDataFrame(buildings_df,geometry='geometry')
var_json = Topology(gdf,prequantize=False).to_json()
data_topojson = alt.InlineData(values = var_json,format = alt.DataFormat(feature = 'data',type = 'topojson'))

In [11]:
# # with open('buildings.geojson','w+') as f:
# #     f.write(gdf.to_json())
# filename = "buildings.geojson"
# file = open(filename)
# df = gpd.read_file(file)

In [12]:
# gdf.to_file(r'C:\Users\ASUS\Desktop\MSc\MSBD 5005\MSBD5005-DataVisualization\PatternsOfLife\buildings.geojson',driver = 'GeoJSON')

In [8]:
cluster_df.loc[cluster_df['pID'] == 1].iloc[0,1]

1

In [38]:
def calculate_efficiency(linestring,time):
    dist = 0
    points = list(linestring.coords)
    for i in range(1,len(points)):
        dist_between_points = abs(points[i][0] - points[i - 1][0]) + abs(points[i][1] - points[i - 1][1])
        dist += dist_between_points
    return dist/time

In [48]:
linestring_dict_efficiency = {}
for id in linestring_dict:
    linestring_dict_efficiency[id] = list()
    for i in linestring_dict[id]:
        try:
            efficiency = calculate_efficiency(linestring_dict[id][i][0].iloc[0,0],linestring_dict[id][i][1])
            linestring_dict_efficiency[id].append((linestring_dict[id][i][0].iloc[0,0],efficiency))
        except:
            continue

In [51]:
linestring_dict_efficiency

{1008: [(<shapely.geometry.linestring.LineString at 0x181ceea6190>,
   88.79888939074425),
  (<shapely.geometry.linestring.LineString at 0x181cd222370>,
   84.14495516416926)],
 833: [],
 342: [(<shapely.geometry.linestring.LineString at 0x181cd2227c0>,
   80.71152253677612),
  (<shapely.geometry.linestring.LineString at 0x181cd222a30>,
   81.87845712512637)],
 538: [(<shapely.geometry.linestring.LineString at 0x181cd222c40>,
   82.72336558459816),
  (<shapely.geometry.linestring.LineString at 0x181cd222eb0>,
   82.21855655351874)],
 216: [(<shapely.geometry.linestring.LineString at 0x181d860c3a0>,
   84.39621986590122),
  (<shapely.geometry.linestring.LineString at 0x181d860c6a0>,
   80.01722296509124)],
 206: [(<shapely.geometry.linestring.LineString at 0x181d860c1c0>,
   84.27209982708115),
  (<shapely.geometry.linestring.LineString at 0x181d860ca90>,
   84.77612929341605)],
 955: [],
 786: [],
 99: [(<shapely.geometry.linestring.LineString at 0x181cd75f730>,
   80.68310762805214),


In [52]:
linestring_dict_efficiency = {i:j for i,j in linestring_dict_efficiency.items() if len(j)!=0}

In [55]:
min = np.inf
max = -100

for i in linestring_dict_efficiency:
    for j in linestring_dict_efficiency[i]:
        if j[1] < min:
            min = j[1]
        if j[1] > max:
            max = j[1]

In [66]:
scale = alt.Scale(domain=[min,max],scheme='turbo')

In [98]:
linestring_list = list()
efficiency = list()
id_list = list()
for id in linestring_dict_efficiency:
    for i in linestring_dict_efficiency[id]:
        linestring_list.append(i[0])
        efficiency.append(i[1])
        id_list.append(id)

In [88]:
min

9.40575809705997

In [91]:
np.linspace(min,max,4)

array([  9.4057581 ,  44.15436251,  78.90296693, 113.65157135])

In [102]:
gdf_linestrings = gpd.GeoDataFrame(pd.DataFrame({'geometry':linestring_list,'efficiency':efficiency,'pID':id_list}),geometry='geometry')

In [101]:
cluster_df

pID  Cluster
0        0        1
1        1        1
2        2        1
3        3        1
4        4        1
...    ...      ...
1006  1006        1
1007  1007        1
1008  1008        1
1009  1009        1
1010  1010        1

[1011 rows x 2 columns]

In [103]:
gdf_linestrings = gdf_linestrings.merge(cluster_df,on = 'pID',how = 'left')

In [104]:
gdf_linestrings

geometry  efficiency   pID  \
0     LINESTRING (-2158.723 2525.142, -1991.311 2787...   88.798889  1008   
1     LINESTRING (1749.108 4023.660, 1330.347 4063.0...   84.144955  1008   
2     LINESTRING (-1202.908 2978.893, -1255.988 2656...   80.711523   342   
3     LINESTRING (-2148.437 5261.789, -1950.086 4927...   81.878457   342   
4     LINESTRING (-1625.863 6198.707, -1691.400 5809...   82.723366   538   
...                                                 ...         ...   ...   
1309  LINESTRING (-2330.422 2982.861, -2434.142 3171...   58.473102   359   
1310  LINESTRING (-2444.635 2576.321, -2416.791 2973...   84.198138   291   
1311  LINESTRING (-1096.084 4912.223, -1057.809 4600...   83.729470   291   
1312  LINESTRING (-3581.037 7172.023, -3726.619 7163...   66.142519   619   
1313  LINESTRING (-3209.738 6522.748, -3522.074 6663...   80.237212   619   

      Cluster  
0           1  
1           1  
2           1  
3           1  
4           1  
...       ...  
1309        1  
1310        1  
1311        1  
1312        1  
1313        1  

[1314 rows x 4 columns]

In [105]:
gdf_linestrings['Efficiency Category'] = np.nan
gdf_linestrings.loc[gdf_linestrings['efficiency']<=44.154,'Efficiency Category'] = 'Low Efficiency'
gdf_linestrings.loc[(gdf_linestrings['efficiency']<=78.90296693) & (gdf_linestrings['efficiency']>44.154),'Efficiency Category'] = 'Efficient'
gdf_linestrings.loc[gdf_linestrings['efficiency']>78.90296693,'Efficiency Category'] = 'High Efficiency'


In [109]:
gdf_low = gdf_linestrings.loc[gdf_linestrings['Efficiency Category'] == 'Low Efficiency']

In [111]:
gdf_low

geometry  efficiency  pID  \
72    LINESTRING (-2988.094 6391.622, -3048.015 6281...   34.099073  687   
73    LINESTRING (-3048.227 6283.815, -2987.882 6388...   33.076989  687   
80     LINESTRING (-185.929 1611.839, -95.944 1511.006)   38.163723  173   
81     LINESTRING (-82.066 1511.113, -199.807 1611.731)   43.672037  173   
104   LINESTRING (-2004.818 4771.622, -1995.316 4689...   18.239858  373   
...                                                 ...         ...  ...   
1236    LINESTRING (529.034 4425.669, 711.962 4411.291)   39.461271  235   
1237    LINESTRING (715.909 4418.132, 525.087 4418.828)   38.303387  235   
1240  LINESTRING (1393.235 4920.768, 1369.933 4872.554)   14.303201   34   
1282    LINESTRING (596.958 3757.221, 647.563 3601.655)   41.234203  131   
1283    LINESTRING (660.207 3610.995, 584.314 3747.882)   42.556104  131   

      Cluster Efficiency Category  
72          1      Low Efficiency  
73          1      Low Efficiency  
80          1      Low Efficiency  
81          1      Low Efficiency  
104         1      Low Efficiency  
...       ...                 ...  
1236        3      Low Efficiency  
1237        3      Low Efficiency  
1240        1      Low Efficiency  
1282        1      Low Efficiency  
1283        1      Low Efficiency  

[125 rows x 5 columns]

In [113]:
background = alt.Chart(data_topojson).mark_geoshape(
    opacity = 0.5
).encode(
    color="properties.buildingType:N"
).project(
    type='identity', reflectY=True
).properties(
    height = 750,width = 750
)
#  alt.Color('Efficiency Category',scale = alt.Scale(range = ['red','yellow','green'],domain = ['Low Efficiency','Efficient','High Efficiency']
efficiency_plot = alt.Chart(gdf_low).mark_geoshape(filled = False,strokeWidth=1,opacity = 0.9,stroke = 'red').properties(
        height = 1000,width = 1000)

alt.layer(background,efficiency_plot).resolve_scale(x = 'shared',y = 'shared')

alt.LayerChart(...)

In [167]:
linestring_list = list()
time = list()
id_list = list()
for id in linestring_dict:
    for i in linestring_dict[id]:
        try:
            linestring_list.append(linestring_dict[id][i][0].iloc[0,0])
            time.append(linestring_dict[id][i][1])
            id_list.append(id)
        except:
            continue

In [168]:
gdf_linestrings = gpd.GeoDataFrame(pd.DataFrame({'geometry':linestring_list,'time':time,'pID':id_list}),geometry='geometry')

In [169]:
idx = list()
for i in range(gdf_linestrings.shape[0]):
    if gdf_linestrings.iloc[i,0].length > 3000:
        idx.append(i)


In [170]:
gdf_linestrings = gdf_linestrings.iloc[idx,:]

In [171]:
gdf_linestrings['time'].describe()

count    454.000000
mean      69.118943
std       23.627797
min       40.000000
25%       50.000000
50%       65.000000
75%       85.000000
max      150.000000
Name: time, dtype: float64

In [172]:
gdf_linestrings.loc[gdf_linestrings['time'] < 50, 'Time Scale'] = 'Low Time Taken'
gdf_linestrings.loc[(gdf_linestrings['time'] >= 50) & (gdf_linestrings['time'] < 85), 'Time Scale'] = 'Average Time Taken'
gdf_linestrings.loc[gdf_linestrings['time'] >= 85, 'Time Scale'] = 'High Time Taken'

In [175]:
gdf_low = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Low Time Taken']
gdf_avg = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Average Time Taken']
gdf_high = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'High Time Taken']

background = alt.Chart(data_topojson).mark_geoshape(
    opacity = 0.5
).encode(
    color="properties.buildingType:N"
).project(
    type='identity', reflectY=True
).properties(
    height = 750,width = 750
)
#  alt.Color('Efficiency Category',scale = alt.Scale(range = ['red','yellow','green'],domain = ['Low Efficiency','Efficient','High Efficiency']
efficiency_plot = alt.Chart(gdf_high).mark_geoshape(filled = False,strokeWidth=1,opacity = 0.5,stroke = 'red').properties(
        height = 1000,width = 1000,title = 'Travel Routes taking over 85 minutes')

alt.layer(background,efficiency_plot).resolve_scale(x = 'shared',y = 'shared')

alt.LayerChart(...)

In [177]:
gdf_low.shape

(86, 4)

In [178]:
gdf_high.shape

(118, 4)

In [179]:
gdf_avg.shape

(250, 4)

In [180]:
gdf_low = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Low Time Taken']
gdf_avg = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Average Time Taken']
gdf_high = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'High Time Taken']

background = alt.Chart(data_topojson).mark_geoshape(
    opacity = 0.5
).encode(
    color="properties.buildingType:N"
).project(
    type='identity', reflectY=True
).properties(
    height = 750,width = 750
)
#  alt.Color('Efficiency Category',scale = alt.Scale(range = ['red','yellow','green'],domain = ['Low Efficiency','Efficient','High Efficiency']
efficiency_plot = alt.Chart(gdf_low).mark_geoshape(filled = False,strokeWidth=1,opacity = 0.5,stroke = 'green').properties(
        height = 1000,width = 1000,title = 'Travel Routes taking less than 50 minutes')

alt.layer(background,efficiency_plot).resolve_scale(x = 'shared',y = 'shared')

alt.LayerChart(...)

In [182]:
gdf_low = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Low Time Taken']
gdf_avg = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'Average Time Taken']
gdf_high = gdf_linestrings.loc[gdf_linestrings['Time Scale'] == 'High Time Taken']

background = alt.Chart(data_topojson).mark_geoshape(
    opacity = 0.5
).encode(
    color="properties.buildingType:N"
).project(
    type='identity', reflectY=True
).properties(
    height = 750,width = 750
)
#  alt.Color('Efficiency Category',scale = alt.Scale(range = ['red','yellow','green'],domain = ['Low Efficiency','Efficient','High Efficiency']
efficiency_plot = alt.Chart(gdf_avg).mark_geoshape(filled = False,strokeWidth=1,opacity = 0.5,stroke = 'purple').properties(
        height = 1000,width = 1000,title = 'Travel Routes taking between 50 and 85 minutes')

alt.layer(background,efficiency_plot).resolve_scale(x = 'shared',y = 'shared')

alt.LayerChart(...)

In [121]:

line_layer_list = list()
for id in linestring_dict:
    for i in linestring_dict[id]:
        # efficiency = i[1]
        # print(efficiency)
        path_json = Topology(linestring_dict[id][i][0],prequantize=False).to_json()
        data_pathjson = alt.InlineData(values = path_json,format=alt.DataFormat(feature = 'data',type = 'topojson'))
        line = alt.Chart(data_pathjson).mark_geoshape(
        fill=None,
        stroke = 'red',
        strokeWidth=1,
        opacity=0.1).properties(
        height = 1000,width = 1000)
        line_layer_list.append(line)

alt.layer(background,*line_layer_list).resolve_scale(x = 'shared',y = 'shared')

alt.LayerChart(...)

In [60]:
i

(<shapely.geometry.linestring.LineString at 0x181ceea6190>, 88.79888939074425)